In [1]:
%matplotlib tk

In [2]:
import numpy as np
import matplotlib.pyplot as plt

from matplotlib import animation, rc
from IPython.display import HTML

import math
import pdb
import time

from scipy.stats import maxwell

## Code from Assignment 1

In [3]:
m_o = 9.1093835611e-31
m_n = 0.26*m_o
nom_sz = 200e-9 * 100e-9
region = (200e-9,100e-9)

boltzmann = 1.3806485279e-23 #in Joules
therm_v = math.sqrt((boltzmann*300)/m_n) # in m/s

tau_mn = 0.2e-12 #ps

mxwell = maxwell()

In [4]:
def P_scattering(dt):
    return 1 - np.exp(-dt/tau_mn)

In [35]:

class AnimatedScatter():
    def __init__(self,region,frames,interval,num_particles=50):
        self.x = np.array([region[0] * np.random.rand() for _ in range(num_particles)])
        self.y = np.array([region[1] * np.random.rand() for _ in range(num_particles)])
        self.vel_x = np.array(therm_v * mxwell.rvs(size=num_particles))
        self.vel_y = np.array(therm_v * mxwell.rvs(size=num_particles))
        
        self.region = region
        #self.data = np.array([x,y,vel_x,vel_y])
        self.numpoints = num_particles
        self.stream = self.data_stream()

        # Setup the figure and axes...
        self.fig, self.ax = plt.subplots()
        # Then setup FuncAnimation.
        #_x = self.data[0, :]
        #_y = self.data[1, :]
        self.colors = [np.random.rand(3,1) for i in range(num_particles)]
        self.scat = self.ax.plot(self.x, self.y, animated=True)[0]
        self.ani = animation.FuncAnimation(self.fig, self.update, 
                                           interval=20,frames=1000, 
                                           blit=True)
        self.ax.set_xlim(0, region[0] + 200e-9)
        self.ax.set_ylim(0, region[1] + 200e-9)

    def setup_plot(self):
        """Initial drawing of the scatter plot."""



        # For FuncAnimation's sake, we need to return the artist we'll be using
        # Note that it expects a sequence of artists, thus the trailing comma.
        return self.scat,

    def data_stream(self):
        """Generate a random walk (brownian motion). Data is scaled to produce
        a soft "flickering" effect."""
        
        num_dots = len(self.x) # assume second dimension holds the particles
        avg_vel = 0
        avg_scattering = 0
        scatter_vec = np.zeros((num_dots))
        while True:
            time = 1e-14
            
            # Boundary Conditions
            #pdb.set_trace()
            # continous x boundary
            print("---------------------")
            print('X1: {}'.format(self.x))
            print('Y1: {}'.format(self.y))
            
            x_mask = self.x < 0
            self.x[x_mask] = region[0]
            
            
            x2_mask = self.x > region[0]
            self.x[x2_mask] = 0
            
            print("X mask: {}".format(x_mask+x2_mask))
            
            #self.x = self.x % self.region[0]
            

            #pdb.set_trace()
            # reflects the particle if it hits top or bottom
            # data[3,:] is y velocity
            
            y_mask = self.y < 0
            self.y[y_mask] = 0
            self.vel_y[y_mask] *= -1
            
            
            y2_mask = self.y > region[1]
            self.y[y2_mask] = region[1]
            self.vel_y[y2_mask] *= -1
            print("Y mask: {}".format(y_mask + y2_mask))
            
            
            
            #self.vel_y = np.where(self.y > region[1],-1*self.vel_y,self.vel_y) # invert Y velocity if out of bounds (top)
            #pdb.set_trace()
                        
            #clip values 
            #self.y = self.y.clip(0,self.region[1])
            print('X2: {}'.format(self.x))
            print('Y2: {}'.format(self.y))
            
            # part 2.2 Scattering with Maxwell Boltzmann rethermalization
            
            '''
            rand_mask = np.random.rand(num_dots)
            mask = P_scattering(time) > rand_mask
            num_positives = len(self.data[2,mask])
            self.data[2,mask] = maxwell().rvs(size=num_positives)*therm_v

            #scatter_vec[mask] = t - scatter_vec[mask] #collect mean time between collision

            rand_mask = np.random.rand(num_dots)
            mask = P_scattering(time) > rand_mask
            num_positives = len(self.data[3,mask])
            self.data[3,mask] = maxwell().rvs(size=num_positives)*therm_v
            '''
            
            
            
            
            self.x += self.vel_x*time #x
            self.y += self.vel_y*time #y
    


            yield self.x,self.y

    def update(self, i):
        
        #velx, vely = self.data[2:, :]
        
        #self.data[0, :] += velx * 1e-9
        #self.data[1, :] += vely * 1e-9
        """Update the scatter plot."""
        x,y = next(self.stream)

        # Set x and y data...
        self.scat.set_data([x,y])
        #self.scat.set_offsets([x,y])
        # We need to return the updated artist for FuncAnimation to draw..
        # Note that it expects a sequence of artists, thus the trailing comma.
        return self.scat,

    def show(self):
        plt.show()

In [36]:
anim1 = AnimatedScatter(region=region,num_particles=7,frames=10,interval=1);

---------------------
X1: [  3.16641989e-08   1.07345552e-07   3.77105424e-08   5.10009599e-09
   6.34377527e-08   1.23777489e-07   1.89938413e-07]
Y1: [  6.70663830e-08   4.38561320e-08   4.01027541e-08   6.99762614e-08
   5.64752301e-08   4.15401168e-08   3.00979831e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  3.16641989e-08   1.07345552e-07   3.77105424e-08   5.10009599e-09
   6.34377527e-08   1.23777489e-07   1.89938413e-07]
Y2: [  6.70663830e-08   4.38561320e-08   4.01027541e-08   6.99762614e-08
   5.64752301e-08   4.15401168e-08   3.00979831e-08]
---------------------
X1: [  3.41342137e-08   1.08732908e-07   4.13093972e-08   7.22649270e-09
   6.62941045e-08   1.26137092e-07   1.92867973e-07]
Y1: [  6.83967483e-08   4.72014917e-08   4.33184085e-08   7.31063345e-08
   5.87644914e-08   4.34123873e-08   3.30592467e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

---------------------
X1: [  6.87144206e-08   1.28155895e-07   9.16933647e-08   3.69960466e-08
   1.06283030e-07   1.59171537e-07   3.22251639e-08]
Y1: [  8.70218625e-08   9.40365286e-08   8.83375688e-08   8.43496342e-08
   9.08141488e-08   6.96241742e-08   7.45169374e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  6.87144206e-08   1.28155895e-07   9.16933647e-08   3.69960466e-08
   1.06283030e-07   1.59171537e-07   3.22251639e-08]
Y2: [  8.70218625e-08   9.40365286e-08   8.83375688e-08   8.43496342e-08
   9.08141488e-08   6.96241742e-08   7.45169374e-08]
---------------------
X1: [  7.11844354e-08   1.29543251e-07   9.52922195e-08   3.91224434e-08
   1.09139381e-07   1.61531140e-07   3.51547243e-08]
Y1: [  8.83522279e-08   9.73818884e-08   9.15532231e-08   8.12195610e-08
   9.31034100e-08   7.14964447e-08   7.74782010e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

---------------------
X1: [  1.05764642e-07   1.48966238e-07   1.45676187e-07   6.88919973e-08
   1.49128307e-07   1.94565586e-07   7.61685693e-08]
Y1: [  9.33481735e-08   5.65103229e-08   6.46278026e-08   3.73985368e-08
   7.71073875e-08   9.77082315e-08   8.22324183e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  1.05764642e-07   1.48966238e-07   1.45676187e-07   6.88919973e-08
   1.49128307e-07   1.94565586e-07   7.61685693e-08]
Y2: [  9.33481735e-08   5.65103229e-08   6.46278026e-08   3.73985368e-08
   7.71073875e-08   9.77082315e-08   8.22324183e-08]
---------------------
X1: [  1.08234657e-07   1.50353595e-07   1.49275042e-07   7.10183940e-08
   1.51984658e-07   1.96925189e-07   7.90981297e-08]
Y1: [  9.20178082e-08   5.31649631e-08   6.14121483e-08   3.42684636e-08
   7.48181263e-08   9.95805020e-08   7.92711547e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

---------------------
X1: [  1.42814864e-07   1.69776582e-07   1.99659009e-07   1.00787948e-07
   1.91973584e-07   2.83152389e-08   1.20111975e-07]
Y1: [  7.33926939e-08   6.32992626e-09   1.63929879e-08   9.39021948e-09
   4.27684689e-08   7.56604836e-08   3.78134640e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  1.42814864e-07   1.69776582e-07   1.99659009e-07   1.00787948e-07
   1.91973584e-07   2.83152389e-08   1.20111975e-07]
Y2: [  7.33926939e-08   6.32992626e-09   1.63929879e-08   9.39021948e-09
   4.27684689e-08   7.56604836e-08   3.78134640e-08]
---------------------
X1: [  1.45284879e-07   1.71163938e-07   2.03257864e-07   1.02914345e-07
   1.94829935e-07   3.06748422e-08   1.23041535e-07]
Y1: [  7.20623286e-08   2.98456648e-09   1.31773336e-08   1.25202926e-08
   4.04792076e-08   7.37882132e-08   3.48522003e-08]
X mask: [False False  True False False False False]
Y mask: [False False False False False False

---------------------
X1: [  1.79865086e-07   1.90586925e-07   5.03839675e-08   1.32683899e-07
   3.42762215e-08   6.37092876e-08   1.64055380e-07]
Y1: [  5.34372143e-08   4.34896771e-08   2.89408888e-08   5.63413169e-08
   8.42955016e-09   4.75764263e-08   5.92252724e-09]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  1.79865086e-07   1.90586925e-07   5.03839675e-08   1.32683899e-07
   3.42762215e-08   6.37092876e-08   1.64055380e-07]
Y2: [  5.34372143e-08   4.34896771e-08   2.89408888e-08   5.63413169e-08
   8.42955016e-09   4.75764263e-08   5.92252724e-09]
---------------------
X1: [  1.82335100e-07   1.91974281e-07   5.39828223e-08   1.34810295e-07
   3.71325733e-08   6.60688908e-08   1.66984940e-07]
Y1: [  5.21068490e-08   4.68350369e-08   3.21565431e-08   5.94713900e-08
   6.14028892e-09   4.57041558e-08   8.88379086e-09]
X mask: [False False False False False False False]
Y mask: [False False False False False False

...

---------------------
X1: [  9.38605616e-08   6.24310296e-08   1.33157628e-07   9.56878520e-08
   1.48530293e-07   4.48324616e-08   7.32390090e-08]
Y1: [  1.55296735e-09  -3.60793293e-10   4.85495310e-08   2.17481710e-08
   1.07188114e-08   3.93176803e-08   6.74261002e-08]
X mask: [False False False False False False False]
Y mask: [False  True False False False False False]
X2: [  9.38605616e-08   6.24310296e-08   1.33157628e-07   9.56878520e-08
   1.48530293e-07   4.48324616e-08   7.32390090e-08]
Y2: [  1.55296735e-09   0.00000000e+00   4.85495310e-08   2.17481710e-08
   1.07188114e-08   3.93176803e-08   6.74261002e-08]
---------------------
X1: [  9.63305764e-08   6.38183858e-08   1.36756483e-07   9.78142487e-08
   1.51386645e-07   4.71920649e-08   7.61685693e-08]
Y1: [  2.22602042e-10   3.34535978e-09   4.53338767e-08   1.86180978e-08
   8.42955016e-09   4.11899508e-08   6.44648365e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

---------------------
X1: [  1.30910783e-07   8.32413728e-08   1.87140451e-07   1.27583803e-07
   1.91375570e-07   8.02265103e-08   1.17182414e-07]
Y1: [  1.72947490e-08   5.01803966e-08   3.14716350e-10   2.50405853e-08
   2.28926125e-08   6.74017376e-08   2.30071459e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  1.30910783e-07   8.32413728e-08   1.87140451e-07   1.27583803e-07
   1.91375570e-07   8.02265103e-08   1.17182414e-07]
Y2: [  1.72947490e-08   5.01803966e-08   3.14716350e-10   2.50405853e-08
   2.28926125e-08   6.74017376e-08   2.30071459e-08]
---------------------
X1: [  1.33380798e-07   8.46287290e-08   1.90739305e-07   1.29710199e-07
   1.94231922e-07   8.25861135e-08   1.20111975e-07]
Y1: [  1.86251143e-08   5.35257564e-08  -2.90093796e-09   2.81706584e-08
   2.51818737e-08   6.92740081e-08   2.00458822e-08]
X mask: [False False False False False False False]
Y mask: [False False  True False False False

---------------------
X1: [  1.67961005e-07   1.04051716e-07   3.95874030e-08   1.59479753e-07
   3.14198698e-08   1.15620559e-07   1.61125820e-07]
Y1: [  3.72502286e-08   1.00360793e-07   4.50191604e-08   7.19916827e-08
   5.72315311e-08   9.54857950e-08   2.07288453e-08]
X mask: [False False False False False False False]
Y mask: [False  True False False False False False]
X2: [  1.67961005e-07   1.04051716e-07   3.95874030e-08   1.59479753e-07
   3.14198698e-08   1.15620559e-07   1.61125820e-07]
Y2: [  3.72502286e-08   1.00000000e-07   4.50191604e-08   7.19916827e-08
   5.72315311e-08   9.54857950e-08   2.07288453e-08]
---------------------
X1: [  1.70431020e-07   1.05439072e-07   4.31862578e-08   1.61606150e-07
   3.42762215e-08   1.17980162e-07   1.64055380e-07]
Y1: [  3.85805939e-08   9.66546402e-08   4.82348147e-08   7.51217558e-08
   5.95207924e-08   9.73580654e-08   2.36901090e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

---------------------
X1: [  4.94002956e-09   1.24862059e-07   9.35702253e-08   1.91375704e-07
   7.42651467e-08   1.51014608e-07   2.92956036e-09]
Y1: [  5.72057082e-08   4.98196034e-08   9.32539750e-08   8.12195610e-08
   9.15704498e-08   7.75327541e-08   6.51477997e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False False]
X2: [  4.94002956e-09   1.24862059e-07   9.35702253e-08   1.91375704e-07
   7.42651467e-08   1.51014608e-07   2.92956036e-09]
Y2: [  5.72057082e-08   4.98196034e-08   9.32539750e-08   8.12195610e-08
   9.15704498e-08   7.75327541e-08   6.51477997e-08]
---------------------
X1: [  7.41004434e-09   1.26249415e-07   9.71690801e-08   1.93502101e-07
   7.71214985e-08   1.53374211e-07   5.85912072e-09]
Y1: [  5.85360735e-08   4.64742436e-08   9.64696293e-08   7.80894879e-08
   9.38597111e-08   7.56604836e-08   6.81090633e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

---------------------
X1: [  4.19902512e-08   1.45672402e-07   1.47553048e-07   2.12639671e-08
   1.17110424e-07   1.86408656e-07   4.68729657e-08]
Y1: [  7.71611878e-08  -3.60793293e-10   6.14121483e-08   3.42684636e-08
   7.48181263e-08   4.94486968e-08   9.11162091e-08]
X mask: [False False False False False False False]
Y mask: [False  True False False False False False]
X2: [  4.19902512e-08   1.45672402e-07   1.47553048e-07   2.12639671e-08
   1.17110424e-07   1.86408656e-07   4.68729657e-08]
Y2: [  7.71611878e-08   0.00000000e+00   6.14121483e-08   3.42684636e-08
   7.48181263e-08   4.94486968e-08   9.11162091e-08]
---------------------
X1: [  4.44602660e-08   1.47059759e-07   1.51151902e-07   2.33903638e-08
   1.19966775e-07   1.88768259e-07   4.98025261e-08]
Y1: [  7.84915531e-08   3.34535978e-09   5.81964940e-08   3.11383905e-08
   7.25288650e-08   4.75764263e-08   8.81549455e-08]
X mask: [False False False False False False False]
Y mask: [False False False False False False

# Part 1

## a)

So with V = 0.1V and the width of the plate is 100nm therefore E = 1000000 N/C


## b)

the force is $$ F = Eq = 1000000 \times 1.60217662e-19 = 
1.60217662e-13 $$


In [ ]:
anim1.data

In [ ]:
anim1.colors

In [13]:
2.33803478e-08 < region[0]

True

In [19]:
ma = np.zeros((5,),'int8')
ma[0] = 1
ma[3] = 1
ma

array([1, 0, 0, 1, 0], dtype=int8)

In [20]:
mb = np.zeros((5,),'int8')
mb[1] = 1
mb[4] = 1
mb

array([0, 1, 0, 0, 1], dtype=int8)

In [28]:
ma ==1

array([ True, False, False,  True, False], dtype=bool)

In [22]:
ta = np.arange(5)

In [24]:
ta

array([0, 1, 2, 3, 4])

In [27]:
ta[np.array([True,False,True,False,False])]

array([0, 2])

In [ ]:
anim1.show()

In [21]:
anim1.ax.plot(anim1.x, anim1.y,c=anim1.colors, animated=True)